In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
import tensorflow as tf
import timeit
import os
from six.moves import cPickle
from text_utils import TextLoader
from tensorflow.contrib import rnn
from char_rnn_model import Model

In [3]:
import tensorflow as tf
from tensorflow.contrib import layers
from tensorflow.contrib import rnn  # rnn stuff temporarily in contrib, moving back to code in TF 1.1
import os
import time
import math
import numpy as np
import my_txtutils as txt
tf.set_random_seed(0)

In [4]:
SEQLEN = 30
BATCHSIZE = 200
ALPHASIZE = txt.ALPHASIZE
INTERNALSIZE = 512
NLAYERS = 3
learning_rate = 0.001  # fixed learning rate
dropout_pkeep = 0.8    # some dropout


shakedir = "shakespeare.txt"
#shakedir = "../tensorflow/**/*.py"
codetext, valitext, bookranges = txt.read_data_files(shakedir, validation=True)

# display some stats on the data
epoch_size = len(codetext) // (BATCHSIZE * SEQLEN)
txt.print_data_stats(len(codetext), len(valitext), epoch_size)

Loading file shakespeare.txt
Training text size is 4.36MB with 0.00KB set aside for validation. There will be 762 batches per epoch


In [5]:
lr = tf.placeholder(tf.float32, name='lr') 
pkeep = tf.placeholder(tf.float32, name='pkeep') 
batchsize = tf.placeholder(tf.int32, name='batchsize')

In [7]:
# inputs
X = tf.placeholder(tf.uint8, [None, None], name='X')    # [ BATCHSIZE, SEQLEN ]
Xo = tf.one_hot(X, ALPHASIZE, 1.0, 0.0)                 # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# expected outputs = same sequence shifted by 1 since we are trying to predict the next character
Y_ = tf.placeholder(tf.uint8, [None, None], name='Y_')  # [ BATCHSIZE, SEQLEN ]
Yo_ = tf.one_hot(Y_, ALPHASIZE, 1.0, 0.0)               # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# input state
Hin = tf.placeholder(tf.float32, [None, INTERNALSIZE*NLAYERS], name='Hin')  # [ BATCHSIZE, INTERNALSIZE * NLAYERS]

In [8]:
cells = [rnn.GRUCell(INTERNALSIZE) for _ in range(NLAYERS)]

dropcells = [rnn.DropoutWrapper(cell,input_keep_prob=pkeep) for cell in cells]
multicell = rnn.MultiRNNCell(dropcells, state_is_tuple=False)
multicell = rnn.DropoutWrapper(multicell, output_keep_prob=pkeep)

Yr, H = tf.nn.dynamic_rnn(multicell, Xo, dtype=tf.float32, initial_state=Hin)

H = tf.identity(H, name='H') 

Instructions for updating:
This class is equivalent as tf.keras.layers.GRUCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
This class is equivalent as tf.keras.layers.StackedRNNCells, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [9]:
Yflat = tf.reshape(Yr, [-1, INTERNALSIZE])    # [ BATCHSIZE x SEQLEN, INTERNALSIZE ]
Ylogits = layers.linear(Yflat, ALPHASIZE)     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Yflat_ = tf.reshape(Yo_, [-1, ALPHASIZE])     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
loss = tf.nn.softmax_cross_entropy_with_logits(logits=Ylogits, labels=Yflat_)  # [ BATCHSIZE x SEQLEN ]
loss = tf.reshape(loss, [batchsize, -1])      # [ BATCHSIZE, SEQLEN ]
Yo = tf.nn.softmax(Ylogits, name='Yo')        # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Y = tf.argmax(Yo, 1)                          # [ BATCHSIZE x SEQLEN ]
Y = tf.reshape(Y, [batchsize, -1], name="Y")  # [ BATCHSIZE, SEQLEN ]
train_step = tf.train.AdamOptimizer(lr).minimize(loss)

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [10]:
# stats for display
seqloss = tf.reduce_mean(loss, 1)
batchloss = tf.reduce_mean(seqloss)
accuracy = tf.reduce_mean(tf.cast(tf.equal(Y_, tf.cast(Y, tf.uint8)), tf.float32))
loss_summary = tf.summary.scalar("batch_loss", batchloss)
acc_summary = tf.summary.scalar("batch_accuracy", accuracy)
summaries = tf.summary.merge([loss_summary, acc_summary])

In [11]:
timestamp = str(math.trunc(time.time()))
summary_writer = tf.summary.FileWriter("log/" + timestamp + "-training")
validation_writer = tf.summary.FileWriter("log/" + timestamp + "-validation")

In [12]:
if not os.path.exists("checkpoints"):
    os.mkdir("checkpoints")
saver = tf.train.Saver(max_to_keep=1000)

In [13]:
DISPLAY_FREQ = 50
_50_BATCHES = DISPLAY_FREQ * BATCHSIZE * SEQLEN
progress = txt.Progress(DISPLAY_FREQ, size=111+2, msg="Training on next "+str(DISPLAY_FREQ)+" batches")

In [14]:
# init
istate = np.zeros([BATCHSIZE, INTERNALSIZE*NLAYERS])  # initial zero input state
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
step = 0

In [15]:
# training loop
for x, y_, epoch in txt.rnn_minibatch_sequencer(codetext, BATCHSIZE, SEQLEN, nb_epochs=10):

    # train on one minibatch
    feed_dict = {X: x, Y_: y_, Hin: istate, lr: learning_rate, pkeep: dropout_pkeep, batchsize: BATCHSIZE}
    _, y, ostate = sess.run([train_step, Y, H], feed_dict=feed_dict)

    # log training data for Tensorboard display a mini-batch of sequences (every 50 batches)
    if step % _50_BATCHES == 0:
        feed_dict = {X: x, Y_: y_, Hin: istate, pkeep: 1.0, batchsize: BATCHSIZE}  # no dropout for validation
        y, l, bl, acc, smm = sess.run([Y, seqloss, batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_learning_learned_comparison(x, y, l, bookranges, bl, acc, epoch_size, step, epoch)
        summary_writer.add_summary(smm, step)

    # run a validation step every 50 batches
    # The validation text should be a single sequence but that's too slow (1s per 1024 chars!),
    # so we cut it up and batch the pieces (slightly inaccurate)
    # tested: validating with 5K sequences instead of 1K is only slightly more accurate, but a lot slower.
    if step % _50_BATCHES == 0 and len(valitext) > 0:
        VALI_SEQLEN = 1*1024  # Sequence length for validation. State will be wrong at the start of each sequence.
        bsize = len(valitext) // VALI_SEQLEN
        txt.print_validation_header(len(codetext), bookranges)
        vali_x, vali_y, _ = next(txt.rnn_minibatch_sequencer(valitext, bsize, VALI_SEQLEN, 1))  # all data in 1 batch
        vali_nullstate = np.zeros([bsize, INTERNALSIZE*NLAYERS])
        feed_dict = {X: vali_x, Y_: vali_y, Hin: vali_nullstate, pkeep: 1.0,  # no dropout for validation
                     batchsize: bsize}
        ls, acc, smm = sess.run([batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_validation_stats(ls, acc)
        # save validation data for Tensorboard
        validation_writer.add_summary(smm, step)

    # display a short text generated with the current weights and biases (every 150 batches)
    if step // 3 % _50_BATCHES == 0:
        txt.print_text_generation_header()
        ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
        rh = np.zeros([1, INTERNALSIZE * NLAYERS])
        for k in range(1000):
            ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
            rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
            print(chr(txt.convert_to_alphabet(rc)), end="")
            ry = np.array([[rc]])
        txt.print_text_generation_footer()

    # save a checkpoint (every 500 batches)
    if step // 10 % _50_BATCHES == 0:
        saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)
        print("Saved file: " + saved_file)

    # display progress bar
    progress.step(reset=step % _50_BATCHES == 0)

    # loop state around
    istate = ostate
    step += BATCHSIZE * SEQLEN


   0 (epoch 0) shakespeare.txt │ First Citizen:\Before we proce │                                │ loss: 4.49779
  30 (epoch 0) shakespeare.txt │ :\O,'tis Marcius!\Let's fetch  │                                │ loss: 4.52533
  60 (epoch 0) shakespeare.txt │ f the nobles.\\SICINIUS:\I wis │                                │ loss: 4.55676
  90 (epoch 0) shakespeare.txt │ u not set them on?\\MENENIUS:\ │                                │ loss: 4.53975
 120 (epoch 0) shakespeare.txt │ temples with the shows of peac │                                │ loss: 4.46889
 150 (epoch 0) shakespeare.txt │ an imagine.\\Third Servingman: │                                │ loss: 4.54264
 180 (epoch 0) shakespeare.txt │ trike the proud cedars 'gainst │                                │ loss: 4.49229
 210 (epoch 0) shakespeare.txt │ 'd imprisonment?\\HASTINGS:\Wi │     eeeeeee                    │ loss: 4.56503
 240 (epoch 0) shakespeare.txt │ my lovely Edward's death,\Thei │ eee                          

,p,,I6Gp,^uepe |paooiee tnsniroostssaareorsiitsaas  t raiiiert otd sJtJososir asaa is  Joario}aao}aerasaor asst} sirs   e  Jrs}it sJsaaossirJd rettrotetitotoe sritatsreoJss, aiiot}o} r} hostiJJe ireeso}irotr sa }ta tesoe eEEtt atrraJJoae t soeietJoJtie JsoJ}ar}asoiJ eor}iJJ sstss }oiia}Jsootieheistt i  iUrt}UaUsio rosia iiis iorts}hieire

itsadrie  orosidor sdidotdrtei  saeaErrioaoeie t tne oaJts tieitraoasJir o aJJ}Jrsatto tJashi roth tstest  rt JJee sd   tetEerie   s toitdddtrtroroeo,ets srs, i ,JesiJosaaJJteJterisn eete<roororo,r oate rssi Jsor}srrriotit aote iaeoaeie anerJtsJe Jtranstrst ,essaei er,,aaiisrs sedtt a aa  areo osdar rrtt ardJiht rthrroeeret  , rraJetioioae edor Joe eJeosrtoeaJroisJ}taJseeri eren,,Jioi,o sdeoosJseora osteaa srsse arJareott  rsasst ehthhesJJJdoodo   Jirro}< ortshesr reJsstr a, e ae tesssdJe ,s sJo  seioisisteeitoaaeddodnoioiidraaesJ,aiJs   oooeosrs}oaJo}sasaiiteJiiiisr}<ete hion seetetn  seJreos,,Js oedooirrd,soa,a Jrt eJe rieattri,d ardJJs tea aJesoaE 

600000 (epoch 0) shakespeare.txt │ ever\Appear in your impediment │ o   \\ o   to e    to          │ loss: 3.21532
600030 (epoch 0) shakespeare.txt │ Condemning some to death, and  │           ho   to e      hh  t │ loss: 2.80712
600060 (epoch 0) shakespeare.txt │ of\ingrateful injury; to repor │ o \          ho      hh ee     │ loss: 3.42471
600090 (epoch 0) shakespeare.txt │ rance; if none, awake\Your dan │       ho ee    hhe             │ loss: 3.16513
600120 (epoch 0) shakespeare.txt │  in the name o' the people\And │ ho ee  te   to te  to     \\   │ loss: 2.72755
600150 (epoch 0) shakespeare.txt │ ut insolent,\O'ercome with pri │ e he        \        toe  eee  │ loss: 3.14312
600180 (epoch 0) shakespeare.txt │ at brought you forth this boy, │   to      h   ho    ee   toe   │ loss: 2.80993
600210 (epoch 0) shakespeare.txt │ bear the corse, and set it dow │ o   to  toe    ho  to  he e    │ loss: 2.56024
600240 (epoch 0) shakespeare.txt │ er; she is lunatic.\\QUEEN MAR │    ho  to te

900000 (epoch 0) shakespeare.txt │ r'd--\\First Citizen:\Well, si │ e  toAORt   aot te  \Ih e  tot │ loss: 3.16018
900030 (epoch 0) shakespeare.txt │  can aid your action.\\MARCIUS │ aerttnt tou  tne nn \\OORRIN:: │ loss: 2.32369
900060 (epoch 0) shakespeare.txt │ m not to be their bedfellow.\W │ eto  thute the sete   re r \\h │ loss: 2.32032
900090 (epoch 0) shakespeare.txt │ e unborn, could never be the m │  to er   torte to e ete the te │ loss: 2.29904
900120 (epoch 0) shakespeare.txt │ out blows! Despising,\For you, │ r  aeere \Io  en t   Ior tou   │ loss: 2.63782
900150 (epoch 0) shakespeare.txt │ nger:\Yes, worthy sir,\The sla │    e Io   tor  e tore Ihe toen │ loss: 2.37967
900180 (epoch 0) shakespeare.txt │ . There's no man in the world\ │ \Ihe   s torteretn the toree \ │ loss: 2.15180
900210 (epoch 0) shakespeare.txt │ ead,\Or earth, gape open wide  │  t  To tote e tore toe ttot  t │ loss: 2.51898
900240 (epoch 0) shakespeare.txt │ the air.\\QUEEN MARGARET:\I'll │ he tnt \\OOR

Soor, mo lorlt womd the ithese aad

I same wathe fonu, Iedorrennoer te sime,
Wams oo me mimiend, fartirasethot thearl s fulromesear t is aeer send to leotin halr ared orid.

Sat soeden, tr tire afs inr mat, the serile m tan siud mouromedis bet fact wot aoe beele ce aand and, I al an iun te wou eodt aor so werer wad sauthar f mart oas aree se them th we me antenre mant theus mf mint
Trtiri heae, bfar oe thime as for ou an as oinge hhe beate thame thu tosu mitle me sre mend ansones isd
Ho thou alas wrare fo wall,
Te su theres tfrtill ye te lin iu thotramit

POOIOIU: Iand bele so s yea toan.

PININER:::
het yea meeth ontard ould mut tos tount,
I too teusretie, bond an or sftor iad,
Hy th anlintin hot farl alt
Wourth it onoume,
Tu s teemesadss wh le mite thame s oleranes.
An danelotos woulr wosis f slile the mulisoe,
Wot ar out inthins thun so wure,
Inas me wom t iod ioe aoddot

Aonlthad there tathir winn
Wor oodes the my mous.

LOTAONNSSI:
Tne, an sin yote,
Har weto we
└──────────────────

...


BENEDICK:
What is the matter?

SIR HUGH EVANS:
Why, the devil he hath been the prince of the counsel of the way.

Servant:
And, sir, the count of York will see him to her head.

Second Murderer:
Why dost thou say there is the matter?

Second Lord:
I will not speak with your hands.

BENEDICK:
Why do you see your lordship seems?

LADY MACBETH:
The king will bear it.

CARDINAL WALSEY:
What is the man? how does he should have heard?

DUKE VINCENTIO:
Well, sir, the gods did with your hands.

CLAUDIO:
And then I say you are a good more.

COUNTESS OF AUVERGNE:
I will not see your hands.

COUNTESS OF AUVERGNE:
I would you will not speak to you.

CARDINAL WOLSEY:
Why dost thou see the count?

CARDINAL WOLSEY:
Well, sir.

SIR TOBY BELCH:

CORIOLANUS:
That is to be a charge, the poor man is no more. But we and
your sister, the grace of the senate of you,
and so shall be a complexion of the charge.

CASSIO:
Well, I will not have.

CORDELIA:
No,
I will be well. I would you 
└──────────────────────

44700000 (epoch 9) shakespeare.txt │ ere none.\\GLOUCESTER:\My lord │ re sote \\CLOUCESTER:\Wy lord, │ loss: 0.62754
44700030 (epoch 9) shakespeare.txt │ s\The manner and the purpose o │ \Tha son er ond the prrpose of │ loss: 0.85796
44700060 (epoch 9) shakespeare.txt │  it.\\BUCKINGHAM:\What says yo │ tt.\\KUCKINGHAM:\What says tou │ loss: 0.54507
44700090 (epoch 9) shakespeare.txt │ h now, two tender playfellows  │  tow  tho hhnder traceullows a │ loss: 1.44549
44700120 (epoch 9) shakespeare.txt │ .\\KING RICHARD III:\Slave, I  │ \\KING HICHARD III:\Woene, s w │ loss: 0.69446
44700150 (epoch 9) shakespeare.txt │ brace each other's love in ban │ race yxch mther s dove as teni │ loss: 1.11857
44700180 (epoch 9) shakespeare.txt │  so sweet a guest\As my sweet  │ temfteat a srist.Tn ta moeet l │ loss: 1.51824
44700210 (epoch 9) shakespeare.txt │ is the Earl of Wiltshire? wher │ s the mnrl of Wanlihire? whare │ loss: 0.91014
44700240 (epoch 9) shakespeare.txt │ ll Norfolk be repeal'd: rep

45000000 (epoch 9) shakespeare.txt │ To those whose dealings have d │ h these thise haat ng  wave ao │ loss: 1.21640
45000030 (epoch 9) shakespeare.txt │ ments,\Being nothing like the  │ ents,\Tu ng tot ing bike ahe w │ loss: 0.88740
45000060 (epoch 9) shakespeare.txt │ s land was guilty of.\Dighton  │  sind ais soilty of \\odnt u t │ loss: 1.62340
45000090 (epoch 9) shakespeare.txt │ vil thus?\\KING RICHARD III:\A │ il toas \\CING HICHARD III:\In │ loss: 0.70141
45000120 (epoch 9) shakespeare.txt │ , now, let Richmond and Elizab │  tot  tit mochaond snd tnezare │ loss: 1.36590
45000150 (epoch 9) shakespeare.txt │  exile:\But little vantage sha │ dyple.\Tut wektle siliage,thal │ loss: 1.26403
45000180 (epoch 9) shakespeare.txt │  met, gentlemen:\I hope the ki │ ya   aontlemen.\I wape the kin │ loss: 1.06857
45000210 (epoch 9) shakespeare.txt │ l our own but death\And that s │  tfr swn pes teath Tnd thet wh │ loss: 1.38877
45000240 (epoch 9) shakespeare.txt │ uld\Learn him forbearance f

Why, how thou dost not stay and stay thy brother God,
That we are there the sea of heaven and the rest of his
sons and the powers of his promised hands, and
his heart, and his hour will not be so like a man of the power o' the word,
therefore, and therefore I had not seen thee to be seen
to be an angry to the poor wind of her heart to the warlike
the world to the poor man of his past and he was
the power of his princes, that thou shouldst
not be a good man that he hath been a man of the
wars that thou shouldst be a money.

CORDELIA:
I will not be a word.

CASSIO:
Why did I so much a soul of this poor man? I
have so born to the king of the poor man in
her pardon, I will be a soldier.

First Lord:
I'll take him well:
Therefore I will be a subtle and to see the way of his part.

COUNTESS:
I will not be a wife of him.

MISTRESS PAGE:
What says you?

CORIOLANUS:
I will not see the king. There is not too lost as they say
the wind of the poon.

COUNTESS:
I would not see thee with
└───────────

45600000 (epoch 9) shakespeare.txt │ ich is no grief to give.\\GLOU │ ch ws totmreef to sove\\\BLOUC │ loss: 0.88111
45600030 (epoch 9) shakespeare.txt │ d up their caps,\And some ten  │  tpothe r fout,\And to e thn t │ loss: 1.27993
45600060 (epoch 9) shakespeare.txt │ be not fix'd in doom perpetual │ eatot soned tn teur orrfecual\ │ loss: 1.59539
45600090 (epoch 9) shakespeare.txt │ KING RICHARD III:\Where is thy │ ING HICHARD III:\Whane is the  │ loss: 0.41008
45600120 (epoch 9) shakespeare.txt │ t, the fair reverence of your  │   thenfotr peserence of tour h │ loss: 0.86723
45600150 (epoch 9) shakespeare.txt │ ceives it is but faintly borne │ o ve  tn in tet toirt y bern \ │ loss: 1.33110
45600180 (epoch 9) shakespeare.txt │ re.\Gentlemen, will you go mus │ e.\\ottlemen, thtl you bo tect │ loss: 0.95964
45600210 (epoch 9) shakespeare.txt │  day.\\HENRY BOLINGBROKE:\So t │ teys\\KELRY BOLINGBROKE:\To th │ loss: 0.84732
45600240 (epoch 9) shakespeare.txt │ ull of water:\That bucket d